In [1]:
import networkx as nx
import sys
import cs6216_taylor_series_identification as TSI
import cs6216_knowledge_graph_creation_and_expansion_experiments as KGCE
import math
import numpy as np
import pandas as pd

In [ ]:
# hyperparameters:

series_length_array = [10, 20, 30, 40, 50, 60, 70, 80, 90, 100]
number_of_samples_array = [100, 200, 300, 400, 500, 600, 700, 800, 900, 1000]

#to store experimental results:
columns = ["series_len", "no_samples", "ans", "sine(X)", "cosine(X)", "quad(X)", "cubic(X)", "X", "exponential(X)"]
experimental_results = pd.DataFrame(columns = columns)
test_list = ["sine(X)", "cosine(X)", "quad(X)", "cubic(X)", "X", "exponential(X)"]

#typical usage: 
for series_length in series_length_array:
    sine_taylor_series = [-1/math.factorial(i)*(i%2 != 0)*((i+1)%4==0)+1/math.factorial(i)*((i+3)%4 == 0) for i in range(series_length)]
    cosine_taylor_series = [1/math.factorial(i)*(i%4 == 0) + -1/math.factorial(i)*((i+2)%4 == 0) for i in range(series_length)]
    quad_taylor_series = [0+1*(i==2) for i in range(series_length)]
    cubic_taylor_series = [0+1*(i==3) for i in range(series_length)]
    expon_taylor_series = [1/math.factorial(i)*(i!=0) for i in range(series_length)]
    X_taylor_series = [0+1*(i==1) for i in range(series_length)]
    for number_of_samples in number_of_samples_array:

        cosine_test_dataframe = TSI.knowledge_dataframe_creation([["cosine", {'taylor_series': cosine_taylor_series}]], 
                                     number_of_samples = number_of_samples, series_length = series_length)
        sine_test_dataframe = TSI.knowledge_dataframe_creation([["sine", {'taylor_series': sine_taylor_series}]], 
                                     number_of_samples = number_of_samples, series_length = series_length)
        quad_test_dataframe = TSI.knowledge_dataframe_creation([["quad", {'taylor_series': quad_taylor_series}]], 
                                     number_of_samples = number_of_samples, series_length = series_length)
        cubic_test_dataframe = TSI.knowledge_dataframe_creation([["cubic", {'taylor_series': cubic_taylor_series}]], 
                                     number_of_samples = number_of_samples, series_length = series_length)
        expon_test_dataframe = TSI.knowledge_dataframe_creation([["expon", {'taylor_series': expon_taylor_series}]], 
                                     number_of_samples = number_of_samples, series_length = series_length)
        X_test_dataframe = TSI.knowledge_dataframe_creation([["X", {'taylor_series': X_taylor_series}]], 
                                     number_of_samples = number_of_samples, series_length = series_length)

        G = KGCE.create_initial_knowledge_graph(series_length)

        nnmodel, scaler_x, scaler_y = TSI.create_neural_network(TSI.knowledge_dataframe_creation([[x,y] for x,y in G.nodes(data = True)], 
                                                                          number_of_samples,series_length), 
                                                                series_length) 
        
        prediction = scaler_y.inverse_transform(nnmodel.predict(scaler_x.transform(cosine_test_dataframe[["input", "output"]].values)))
        answer_pct = [series_length, number_of_samples, "cosine"]
        percentage = TSI.match_prediction_to_series(prediction, [[x,y] for x,y in G.nodes(data = True)])
        for i in test_list:
            answer_pct.append(sum(list(map(int, percentage == i)))/len(percentage))
        answer_pct = np.asarray(answer_pct)
        experimental_results = experimental_results.append(pd.DataFrame(answer_pct.reshape(1,-1), columns=list(experimental_results)), ignore_index=True)
        
        prediction = scaler_y.inverse_transform(nnmodel.predict(scaler_x.transform(sine_test_dataframe[["input", "output"]].values)))
        answer_pct = [series_length, number_of_samples, "sine"]
        percentage = TSI.match_prediction_to_series(prediction, [[x,y] for x,y in G.nodes(data = True)])
        for i in test_list:
            answer_pct.append(sum(list(map(int, percentage == i)))/len(percentage))
        answer_pct = np.asarray(answer_pct)
        experimental_results = experimental_results.append(pd.DataFrame(answer_pct.reshape(1,-1), columns=list(experimental_results)), ignore_index=True)
        
        prediction = scaler_y.inverse_transform(nnmodel.predict(scaler_x.transform(quad_test_dataframe[["input", "output"]].values)))
        answer_pct = [series_length, number_of_samples, "quad"]
        percentage = TSI.match_prediction_to_series(prediction, [[x,y] for x,y in G.nodes(data = True)])
        for i in test_list:
            answer_pct.append(sum(list(map(int, percentage == i)))/len(percentage))
        answer_pct = np.asarray(answer_pct)
        experimental_results = experimental_results.append(pd.DataFrame(answer_pct.reshape(1,-1), columns=list(experimental_results)), ignore_index=True)

        
        cubic_results = scaler_y.inverse_transform(nnmodel.predict(scaler_x.transform(cubic_test_dataframe[["input", "output"]].values)))
        answer_pct = [series_length, number_of_samples, "cubic"]
        percentage = TSI.match_prediction_to_series(prediction, [[x,y] for x,y in G.nodes(data = True)])
        for i in test_list:
            answer_pct.append(sum(list(map(int, percentage == i)))/len(percentage))
        answer_pct = np.asarray(answer_pct)
        experimental_results = experimental_results.append(pd.DataFrame(answer_pct.reshape(1,-1), columns=list(experimental_results)), ignore_index=True)   
        
        expon_results = scaler_y.inverse_transform(nnmodel.predict(scaler_x.transform(expon_test_dataframe[["input", "output"]].values)))
        answer_pct = [series_length, number_of_samples, "expon"]
        percentage = TSI.match_prediction_to_series(prediction, [[x,y] for x,y in G.nodes(data = True)])
        for i in test_list:
            answer_pct.append(sum(list(map(int, percentage == i)))/len(percentage))
        answer_pct = np.asarray(answer_pct)
        experimental_results = experimental_results.append(pd.DataFrame(answer_pct.reshape(1,-1), columns=list(experimental_results)), ignore_index=True)
        
        X_results = scaler_y.inverse_transform(nnmodel.predict(scaler_x.transform(X_test_dataframe[["input", "output"]].values)))
        answer_pct = [series_length, number_of_samples, "X"]
        percentage = TSI.match_prediction_to_series(prediction, [[x,y] for x,y in G.nodes(data = True)])
        for i in test_list:
            answer_pct.append(sum(list(map(int, percentage == i)))/len(percentage))
        answer_pct = np.asarray(answer_pct)
        experimental_results = experimental_results.append(pd.DataFrame(answer_pct.reshape(1,-1), columns=list(experimental_results)), ignore_index=True)

print(experimental_results)
experimental_results.to_csv("experimental_results_one_step_range0-10.csv", index=False)

/home/ziyu/.pyenv/versions/3.7.7/lib/python3.7/site-packages/pandas/core/frame.py:6692: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  sort=sort)


Model: "sequential"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense (Dense)                (None, 32)                96        
_________________________________________________________________
dense_1 (Dense)              (None, 64)                2112      
_________________________________________________________________
dense_2 (Dense)              (None, 100)               6500      
_________________________________________________________________
dense_3 (Dense)              (None, 128)               12928     
_________________________________________________________________
dense_4 (Dense)              (None, 150)               19350     
_________________________________________________________________
dropout (Dropout)            (None, 150)               0         
_________________________________________________________________
dense_5 (Dense)              (None, 256)               3

Epoch 32/200
8/8 [==============================] - 0s 4ms/step - loss: 0.1608 - mse: 0.1608 - mae: 0.3358 - maape: 0.9515 - val_loss: 0.1655 - val_mse: 0.1655 - val_mae: 0.3385 - val_maape: 0.9328
Epoch 33/200
8/8 [==============================] - 0s 4ms/step - loss: 0.1594 - mse: 0.1594 - mae: 0.3292 - maape: 0.9511 - val_loss: 0.1636 - val_mse: 0.1636 - val_mae: 0.3322 - val_maape: 0.9328
Epoch 34/200
8/8 [==============================] - 0s 4ms/step - loss: 0.1582 - mse: 0.1582 - mae: 0.3260 - maape: 0.9539 - val_loss: 0.1620 - val_mse: 0.1620 - val_mae: 0.3309 - val_maape: 0.9367
Epoch 35/200
8/8 [==============================] - 0s 4ms/step - loss: 0.1583 - mse: 0.1583 - mae: 0.3284 - maape: 0.9482 - val_loss: 0.1610 - val_mse: 0.1610 - val_mae: 0.3310 - val_maape: 0.9440
Epoch 36/200
8/8 [==============================] - 0s 4ms/step - loss: 0.1572 - mse: 0.1572 - mae: 0.3254 - maape: 0.9625 - val_loss: 0.1649 - val_mse: 0.1649 - val_mae: 0.3285 - val_maape: 0.9478
Epoch 37/2

8/8 [==============================] - 0s 5ms/step - loss: 0.1523 - mse: 0.1523 - mae: 0.3268 - maape: 0.9487 - val_loss: 0.1580 - val_mse: 0.1580 - val_mae: 0.3209 - val_maape: 0.9334
Epoch 74/200
8/8 [==============================] - 0s 5ms/step - loss: 0.1531 - mse: 0.1531 - mae: 0.3129 - maape: 0.9499 - val_loss: 0.1555 - val_mse: 0.1555 - val_mae: 0.3256 - val_maape: 0.9346
Epoch 75/200
8/8 [==============================] - 0s 5ms/step - loss: 0.1524 - mse: 0.1524 - mae: 0.3235 - maape: 0.9518 - val_loss: 0.1606 - val_mse: 0.1606 - val_mae: 0.3277 - val_maape: 0.9472
Epoch 76/200
8/8 [==============================] - 0s 4ms/step - loss: 0.1571 - mse: 0.1571 - mae: 0.3195 - maape: 0.9687 - val_loss: 0.1653 - val_mse: 0.1653 - val_mae: 0.3361 - val_maape: 0.9545
Epoch 77/200
8/8 [==============================] - 0s 4ms/step - loss: 0.1562 - mse: 0.1562 - mae: 0.3315 - maape: 0.9616 - val_loss: 0.1550 - val_mse: 0.1550 - val_mae: 0.3349 - val_maape: 0.9466
Epoch 78/200
8/8 [=====

8/8 [==============================] - 0s 4ms/step - loss: 0.1496 - mse: 0.1496 - mae: 0.3106 - maape: 0.9497 - val_loss: 0.1524 - val_mse: 0.1524 - val_mae: 0.3188 - val_maape: 0.9382
Epoch 115/200
8/8 [==============================] - 0s 4ms/step - loss: 0.1452 - mse: 0.1452 - mae: 0.3100 - maape: 0.9512 - val_loss: 0.1513 - val_mse: 0.1513 - val_mae: 0.3245 - val_maape: 0.9342
Epoch 116/200
8/8 [==============================] - 0s 4ms/step - loss: 0.1530 - mse: 0.1530 - mae: 0.3173 - maape: 0.9527 - val_loss: 0.1613 - val_mse: 0.1613 - val_mae: 0.3309 - val_maape: 0.9451
Epoch 117/200
8/8 [==============================] - 0s 4ms/step - loss: 0.1516 - mse: 0.1516 - mae: 0.3228 - maape: 0.9386 - val_loss: 0.1565 - val_mse: 0.1565 - val_mae: 0.3393 - val_maape: 0.9409
Epoch 118/200
8/8 [==============================] - 0s 4ms/step - loss: 0.1512 - mse: 0.1512 - mae: 0.3267 - maape: 0.9454 - val_loss: 0.1543 - val_mse: 0.1543 - val_mae: 0.3178 - val_maape: 0.9307
Epoch 119/200
8/8 [

...

Epoch 155/200
57/57 [==============================] - 0s 3ms/step - loss: 0.1119 - mse: 0.1119 - mae: 0.2553 - maape: 0.8106 - val_loss: 0.1082 - val_mse: 0.1082 - val_mae: 0.2395 - val_maape: 0.7852
Epoch 156/200
57/57 [==============================] - 0s 3ms/step - loss: 0.1099 - mse: 0.1099 - mae: 0.2522 - maape: 0.8036 - val_loss: 0.1157 - val_mse: 0.1157 - val_mae: 0.2276 - val_maape: 0.7858
Epoch 157/200
57/57 [==============================] - 0s 2ms/step - loss: 0.1124 - mse: 0.1124 - mae: 0.2564 - maape: 0.8118 - val_loss: 0.1102 - val_mse: 0.1102 - val_mae: 0.2474 - val_maape: 0.7927
Epoch 158/200
57/57 [==============================] - 0s 3ms/step - loss: 0.1062 - mse: 0.1062 - mae: 0.2463 - maape: 0.8032 - val_loss: 0.1057 - val_mse: 0.1057 - val_mae: 0.2452 - val_maape: 0.8015
Epoch 159/200
57/57 [==============================] - 0s 2ms/step - loss: 0.1122 - mse: 0.1122 - mae: 0.2577 - maape: 0.8079 - val_loss: 0.1077 - val_mse: 0.1077 - val_mae: 0.2395 - val_maape: 0.

Epoch 196/200
57/57 [==============================] - 0s 2ms/step - loss: 0.1083 - mse: 0.1083 - mae: 0.2512 - maape: 0.8085 - val_loss: 0.1154 - val_mse: 0.1154 - val_mae: 0.2778 - val_maape: 0.8318
Epoch 197/200
57/57 [==============================] - 0s 2ms/step - loss: 0.1059 - mse: 0.1059 - mae: 0.2480 - maape: 0.8062 - val_loss: 0.0965 - val_mse: 0.0965 - val_mae: 0.2093 - val_maape: 0.7792
Epoch 198/200
57/57 [==============================] - 0s 2ms/step - loss: 0.1092 - mse: 0.1092 - mae: 0.2545 - maape: 0.8108 - val_loss: 0.1112 - val_mse: 0.1112 - val_mae: 0.2519 - val_maape: 0.8048
Epoch 199/200
57/57 [==============================] - 0s 2ms/step - loss: 0.1095 - mse: 0.1095 - mae: 0.2533 - maape: 0.8069 - val_loss: 0.1126 - val_mse: 0.1126 - val_mae: 0.2553 - val_maape: 0.8035
Epoch 200/200
57/57 [==============================] - 0s 2ms/step - loss: 0.1080 - mse: 0.1080 - mae: 0.2522 - maape: 0.8104 - val_loss: 0.1057 - val_mse: 0.1057 - val_mae: 0.2352 - val_maape: 0.

/home/ziyu/.pyenv/versions/3.7.7/lib/python3.7/site-packages/pandas/core/frame.py:6692: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  sort=sort)


Model: "sequential_98"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_980 (Dense)            (None, 32)                96        
_________________________________________________________________
dense_981 (Dense)            (None, 64)                2112      
_________________________________________________________________
dense_982 (Dense)            (None, 100)               6500      
_________________________________________________________________
dense_983 (Dense)            (None, 128)               12928     
_________________________________________________________________
dense_984 (Dense)            (None, 150)               19350     
_________________________________________________________________
dropout_294 (Dropout)        (None, 150)               0         
_________________________________________________________________
dense_985 (Dense)            (None, 256)             

Epoch 32/200
65/65 [==============================] - 0s 2ms/step - loss: 0.1214 - mse: 0.1214 - mae: 0.2684 - maape: 0.8113 - val_loss: 0.1263 - val_mse: 0.1263 - val_mae: 0.2718 - val_maape: 0.8111
Epoch 33/200
65/65 [==============================] - 0s 2ms/step - loss: 0.1223 - mse: 0.1223 - mae: 0.2707 - maape: 0.8091 - val_loss: 0.1241 - val_mse: 0.1241 - val_mae: 0.2704 - val_maape: 0.8107
Epoch 34/200
65/65 [==============================] - 0s 2ms/step - loss: 0.1218 - mse: 0.1218 - mae: 0.2701 - maape: 0.8111 - val_loss: 0.1282 - val_mse: 0.1282 - val_mae: 0.2770 - val_maape: 0.8098
Epoch 35/200
65/65 [==============================] - 0s 3ms/step - loss: 0.1257 - mse: 0.1257 - mae: 0.2746 - maape: 0.8103 - val_loss: 0.1238 - val_mse: 0.1238 - val_mae: 0.2639 - val_maape: 0.8120
Epoch 36/200
65/65 [==============================] - 0s 3ms/step - loss: 0.1219 - mse: 0.1219 - mae: 0.2692 - maape: 0.8101 - val_loss: 0.1225 - val_mse: 0.1225 - val_mae: 0.2645 - val_maape: 0.8060
